In [1]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import Sequential
from tensorflow.keras import utils, datasets, layers, models, Model, regularizers
from tensorflow.keras.layers import Input, Dense, Dropout, Flatten, BatchNormalization, GlobalAveragePooling2D
from tensorflow.keras.layers import Layer
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers.experimental import preprocessing
from tensorflow.keras.callbacks import Callback, EarlyStopping, ModelCheckpoint, ReduceLROnPlateau
from tensorflow.keras import mixed_precision
from sklearn.model_selection import train_test_split
import os
import json
from tqdm import tqdm
import cv2  # pip install opencv-python
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import glob
from IPython.display import clear_output

In [2]:
dir = ""

### Modeling - EfficientNetB4

In [ ]:
### training and validation data
BATCH_SIZE = 256
IMAGE_SIZE = (224, 224)

train_generator = ImageDataGenerator(
    preprocessing_function = tf.keras.applications.efficientnet.preprocess_input,
    zoom_range = 0.3, 
    brightness_range = [0.8,1.2], 
    horizontal_flip = True
)

valid_generator = ImageDataGenerator(
    preprocessing_function = tf.keras.applications.efficientnet.preprocess_input,
)

train_images = train_generator.flow_from_directory(
    directory = dir+'train',
    target_size = IMAGE_SIZE,
    color_mode = 'rgb',
    class_mode = 'categorical',
    batch_size = BATCH_SIZE,
    shuffle = True,
    seed = 7,
)

valid_images = valid_generator.flow_from_directory(
    directory = dir+'valid',
    target_size = IMAGE_SIZE,
    color_mode = 'rgb',
    class_mode = 'categorical',
    batch_size = BATCH_SIZE,
    shuffle = False
)

In [ ]:
# Load the pretained model
pretrained_model = tf.keras.applications.EfficientNetB4(
    input_shape = (224, 224, 3),
    include_top = False,
    weights = 'imagenet',
    pooling = 'max',
)

for i in range(430):
    pretrained_model.layers[i].trainable = False

for i in range(430, 475):
    pretrained_model.layers[i].trainable = True

In [10]:
pretrained_model.summary()

Model: "efficientnetb4"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_1 (InputLayer)        [(None, 224, 224, 3)]        0         []                            
                                                                                                  
 rescaling (Rescaling)       (None, 224, 224, 3)          0         ['input_1[0][0]']             
                                                                                                  
 normalization (Normalizati  (None, 224, 224, 3)          7         ['rescaling[0][0]']           
 on)                                                                                              
                                                                                                  
 rescaling_1 (Rescaling)     (None, 224, 224, 3)          0         ['normalization[0

                                                                                                  
 block2a_expand_conv (Conv2  (None, 112, 112, 144)        3456      ['block1b_add[0][0]']         
 D)                                                                                               
                                                                                                  
 block2a_expand_bn (BatchNo  (None, 112, 112, 144)        576       ['block2a_expand_conv[0][0]'] 
 rmalization)                                                                                     
                                                                                                  
 block2a_expand_activation   (None, 112, 112, 144)        0         ['block2a_expand_bn[0][0]']   
 (Activation)                                                                                     
                                                                                                  
 block2a_d

 block2c_expand_conv (Conv2  (None, 56, 56, 192)          6144      ['block2b_add[0][0]']         
 D)                                                                                               
                                                                                                  
 block2c_expand_bn (BatchNo  (None, 56, 56, 192)          768       ['block2c_expand_conv[0][0]'] 
 rmalization)                                                                                     
                                                                                                  
 block2c_expand_activation   (None, 56, 56, 192)          0         ['block2c_expand_bn[0][0]']   
 (Activation)                                                                                     
                                                                                                  
 block2c_dwconv (DepthwiseC  (None, 56, 56, 192)          1728      ['block2c_expand_activation[0]
 onv2D)   

                                                                                                  
 block3a_expand_conv (Conv2  (None, 56, 56, 192)          6144      ['block2d_add[0][0]']         
 D)                                                                                               
                                                                                                  
 block3a_expand_bn (BatchNo  (None, 56, 56, 192)          768       ['block3a_expand_conv[0][0]'] 
 rmalization)                                                                                     
                                                                                                  
 block3a_expand_activation   (None, 56, 56, 192)          0         ['block3a_expand_bn[0][0]']   
 (Activation)                                                                                     
                                                                                                  
 block3a_d

 block3c_expand_conv (Conv2  (None, 28, 28, 336)          18816     ['block3b_add[0][0]']         
 D)                                                                                               
                                                                                                  
 block3c_expand_bn (BatchNo  (None, 28, 28, 336)          1344      ['block3c_expand_conv[0][0]'] 
 rmalization)                                                                                     
                                                                                                  
 block3c_expand_activation   (None, 28, 28, 336)          0         ['block3c_expand_bn[0][0]']   
 (Activation)                                                                                     
                                                                                                  
 block3c_dwconv (DepthwiseC  (None, 28, 28, 336)          8400      ['block3c_expand_activation[0]
 onv2D)   

...

 D)                                                                                               
                                                                                                  
 block6c_expand_bn (BatchNo  (None, 7, 7, 1632)           6528      ['block6c_expand_conv[0][0]'] 
 rmalization)                                                                                     
                                                                                                  
 block6c_expand_activation   (None, 7, 7, 1632)           0         ['block6c_expand_bn[0][0]']   
 (Activation)                                                                                     
                                                                                                  
 block6c_dwconv (DepthwiseC  (None, 7, 7, 1632)           40800     ['block6c_expand_activation[0]
 onv2D)                                                             [0]']                         
          

 block6e_expand_conv (Conv2  (None, 7, 7, 1632)           443904    ['block6d_add[0][0]']         
 D)                                                                                               
                                                                                                  
 block6e_expand_bn (BatchNo  (None, 7, 7, 1632)           6528      ['block6e_expand_conv[0][0]'] 
 rmalization)                                                                                     
                                                                                                  
 block6e_expand_activation   (None, 7, 7, 1632)           0         ['block6e_expand_bn[0][0]']   
 (Activation)                                                                                     
                                                                                                  
 block6e_dwconv (DepthwiseC  (None, 7, 7, 1632)           40800     ['block6e_expand_activation[0]
 onv2D)   

                                                                                                  
 block6g_expand_conv (Conv2  (None, 7, 7, 1632)           443904    ['block6f_add[0][0]']         
 D)                                                                                               
                                                                                                  
 block6g_expand_bn (BatchNo  (None, 7, 7, 1632)           6528      ['block6g_expand_conv[0][0]'] 
 rmalization)                                                                                     
                                                                                                  
 block6g_expand_activation   (None, 7, 7, 1632)           0         ['block6g_expand_bn[0][0]']   
 (Activation)                                                                                     
                                                                                                  
 block6g_d

                                                                     'block6g_add[0][0]']         
                                                                                                  
 block7a_expand_conv (Conv2  (None, 7, 7, 1632)           443904    ['block6h_add[0][0]']         
 D)                                                                                               
                                                                                                  
 block7a_expand_bn (BatchNo  (None, 7, 7, 1632)           6528      ['block7a_expand_conv[0][0]'] 
 rmalization)                                                                                     
                                                                                                  
 block7a_expand_activation   (None, 7, 7, 1632)           0         ['block7a_expand_bn[0][0]']   
 (Activation)                                                                                     
          

 top_bn (BatchNormalization  (None, 7, 7, 1792)           7168      ['top_conv[0][0]']            
 )                                                                                                
                                                                                                  
 top_activation (Activation  (None, 7, 7, 1792)           0         ['top_bn[0][0]']              
 )                                                                                                
                                                                                                  
 max_pool (GlobalMaxPooling  (None, 1792)                 0         ['top_activation[0][0]']      
 2D)                                                                                              
                                                                                                  
Total params: 17673823 (67.42 MB)
Trainable params: 5991832 (22.86 MB)
Non-trainable params: 11681991 (44.56 

In [ ]:
model_ENB4 = Sequential([
    Input((224, 224, 3), name = 'inputLayer'),
    pretrained_model,
    Dense(350, activation = 'relu'),
    BatchNormalization(),
    Dropout(0.25),
    Dense(100, activation = 'softmax', dtype = tf.float32)
  ])

model_ENB4.summary()

In [ ]:
### 先跑一次epoch=25發現不夠，再跑一次epoch=25，到epoch=39停止
model_ENB4.compile(optimizer = Adam(0.0001), loss = 'categorical_crossentropy', metrics = ['accuracy'])

history1 = model_ENB4.fit(train_images,
            epochs = 50,
            batch_size = 256,
            validation_data = valid_images,
            callbacks=[
                EarlyStopping(monitor = "val_loss", 
                                       patience = 3,
                                       restore_best_weights = True), 
                ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=2, mode='min') 
            ])

# save model
model_ENB4.save(dir+'model/model5_EfficientNetB4.h5')

### Modeling - EfficientNetV2B1

In [ ]:
%%time

# 讀train/validation data (無 rescale)
BATCH_SIZE = 256
IMAGE_SIZE = (224, 224)

train_generator = ImageDataGenerator(
    #rescale = 1./255,
    preprocessing_function = tf.keras.applications.efficientnet.preprocess_input,
    width_shift_range=0.2, #水平偏移
    height_shift_range=0.2, #垂直偏移
    zoom_range=0.2, #放大部分圖片
    horizontal_flip=True #水平翻轉
    # there could be image augmentation here
)

valid_generator = ImageDataGenerator(
    #rescale = 1./255,
    preprocessing_function = tf.keras.applications.efficientnet.preprocess_input,
)

# Split the data into three categories.
train_images = train_generator.flow_from_directory(
    directory = dir+'train',
    target_size = IMAGE_SIZE,
    color_mode = 'rgb',
    class_mode = 'categorical',
    batch_size = BATCH_SIZE,
    shuffle = True,
    seed = 42,
)

valid_images = valid_generator.flow_from_directory(
    directory = dir+'valid',
    target_size = IMAGE_SIZE,
    color_mode = 'rgb',
    class_mode = 'categorical',
    batch_size = BATCH_SIZE,
    shuffle = False
)

In [ ]:
# Load the pretained model
pretrained_model = tf.keras.applications.EfficientNetV2B1(
    input_shape = (224, 224, 3),
    include_top = False,
    weights = 'imagenet',
    pooling = 'max',
)

for i in range(300):
    #print(i)
    pretrained_model.layers[i].trainable = False
    
for i in range(300, 335):
    #print(i)
    pretrained_model.layers[i].trainable = True

In [13]:
pretrained_model.summary()

Model: "efficientnetv2-b1"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_1 (InputLayer)        [(None, 224, 224, 3)]        0         []                            
                                                                                                  
 rescaling (Rescaling)       (None, 224, 224, 3)          0         ['input_1[0][0]']             
                                                                                                  
 normalization (Normalizati  (None, 224, 224, 3)          0         ['rescaling[0][0]']           
 on)                                                                                              
                                                                                                  
 stem_conv (Conv2D)          (None, 112, 112, 32)         864       ['normalizatio

In [ ]:
model_ENV2B1 = Sequential([
    Input((224, 224, 3), name = 'inputLayer'),
    pretrained_model,
    Dense(350, activation = 'relu'),
    BatchNormalization(),
    Dropout(0.25),
    Dense(100, activation = 'softmax', dtype = tf.float32)
  ])

model_ENV2B1.summary()

In [ ]:
model_ENV2B1.compile(optimizer = Adam(0.0001), loss = 'categorical_crossentropy', metrics = ['accuracy'])

history2 = model_ENV2B1.fit(train_images,
            epochs = 25,
            batch_size = 256,
            validation_data = valid_images) 

# save model
model_ENV2B1.save(dir+'model/model5_EfficientNetV2B1.h5')

### Modeling - EfficientNetV2S

In [ ]:
%%time

BATCH_SIZE = 256
IMAGE_SIZE = (224, 224)

generator_train = ImageDataGenerator(
    #rescale = 1./255,
    preprocessing_function = tf.keras.applications.efficientnet_v2.preprocess_input,
    horizontal_flip = True
)
generator_valid = ImageDataGenerator(
    #rescale = 1./255,
    preprocessing_function = tf.keras.applications.efficientnet_v2.preprocess_input
)

# Split the data into three categories.
train_images = generator_train.flow_from_directory(
    directory = dir+'achieve/train',
    target_size = IMAGE_SIZE,
    color_mode = 'rgb',
    class_mode = 'categorical',
    batch_size = BATCH_SIZE,
    shuffle = True,
    seed = 42,
)
print(len(train_images))

valid_images = generator_valid.flow_from_directory(
    directory = dir+'achieve/valid',
    target_size = IMAGE_SIZE,
    color_mode = 'rgb',
    class_mode = 'categorical',
    batch_size = BATCH_SIZE,
    shuffle = False
)
print(len(valid_images))

In [ ]:
ENV2S = tf.keras.applications.EfficientNetV2S(
    input_shape= (224, 224, 3),
    include_top= False,
    weights= "imagenet"
)

# 513 layers
for i, layer in enumerate(ENV2S.layers):
    if i <= 300:
        ENV2S.layers[i].trainable = False

ENV2S.summary()

In [ ]:
model_ENV2S = Sequential([
    ENV2S,
    GlobalAveragePooling2D(),
    Dense(512, kernel_regularizer= regularizers.l2(0.016), activity_regularizer= regularizers.l1(0.006),
          bias_regularizer= regularizers.l1(0.006), activation= 'relu'),
    BatchNormalization(axis= -1, momentum= 0.99, epsilon= 0.001),
    Dropout(0.5),
    Dense(100, activation = 'softmax', dtype = tf.float32)
  ])

model_ENV2S.summary()

In [ ]:
model_ENV2S.compile(optimizer = Adam(0.0005), loss = 'categorical_crossentropy', metrics = ['accuracy'])

history3 = model_ENV2S.fit(train_images,
            epochs = 50,
            batch_size = 256,
            validation_data = valid_images,
            callbacks=[EarlyStopping(monitor = "val_loss", # watch the val loss metric
                                     patience = 10,
                                     restore_best_weights = True),
                       ReduceLROnPlateau(monitor = 'val_loss', factor = 0.2, patience = 2, mode = 'min')]
            )

# save model
model_ENV2S.save(dir+'model/model4_ENV2S.h5')

### 合併結果

In [4]:
# 類別名稱
class_names = os.listdir(dir+'achieve/train')
class_names.sort()
class_names_label = {class_name:i for i, class_name in enumerate(class_names)}

In [5]:
# 讀 test data
test_images = []
for i in range(500):
    img = cv2.imread(dir+'achieve/test/'+str(i)+'.jpg')
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB) #由BGR轉RGB
    test_images.append(img)

test_images = np.array(test_images)
test_images.shape

(500, 224, 224, 3)

In [6]:
from tensorflow.keras.models import load_model

# 讀模型
model_ENB4 = load_model(dir+'model/model5_EfficientNetB4.h5', compile = False)
model_ENV2B1 = load_model(dir+'model/model5_EfficientNetV2B1.h5', compile = False)
model_ENV2S = load_model(dir+'model/model4_ENV2S.h5', compile = False)

In [7]:
# 模型結構
print("Model EfficientNetB4")
model_ENB4.summary()

# 模型 weights
model_ENB4.weights

Model EfficientNetB4
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 efficientnetb4 (Functional)  (None, 1792)             17673823  
                                                                 
 dense (Dense)               (None, 350)               627550    
                                                                 
 batch_normalization (BatchN  (None, 350)              1400      
 ormalization)                                                   
                                                                 
 dropout (Dropout)           (None, 350)               0         
                                                                 
 dense_1 (Dense)             (None, 100)               35100     
                                                                 
Total params: 18,337,873
Trainable params: 6,655,182
Non-trainable params: 11,682,691
_______________

[<tf.Variable 'normalization/mean:0' shape=(3,) dtype=float32, numpy=array([0.485, 0.456, 0.406], dtype=float32)>,
 <tf.Variable 'normalization/variance:0' shape=(3,) dtype=float32, numpy=array([0.229, 0.224, 0.225], dtype=float32)>,
 <tf.Variable 'normalization/count:0' shape=() dtype=int64, numpy=0>,
 <tf.Variable 'stem_conv/kernel:0' shape=(3, 3, 3, 48) dtype=float32, numpy=
 array([[[[ 2.20859125e-02, -3.54408383e-01,  2.98673540e-01, ...,
            6.43759593e-02,  2.34505665e-02,  4.39255893e-01],
          [-3.61267403e-02, -7.12899044e-02,  1.16172409e+00, ...,
            5.87348402e-01, -5.32432683e-02,  1.18248723e-01],
          [ 5.13000607e-01,  4.16596770e-01,  2.34334469e-01, ...,
            6.27864450e-02, -6.46309376e-01, -8.16539675e-02]],
 
         [[-1.46005638e-02, -5.61126351e-01,  4.57988791e-02, ...,
            1.55987814e-01, -9.91783515e-02,  5.74809253e-01],
          [ 3.91144641e-02, -1.02806643e-01,  3.46348703e-01, ...,
            4.67721641e-01, -

In [8]:
# 模型結構
print("Model EfficientNetV2B1")
model_ENV2B1.summary()

# 模型 weights
model_ENV2B1.weights

Model EfficientNetV2B1
Model: "sequential_7"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 efficientnetv2-b1 (Function  (None, 1280)             6931124   
 al)                                                             
                                                                 
 dense_14 (Dense)            (None, 350)               448350    
                                                                 
 batch_normalization_7 (Batc  (None, 350)              1400      
 hNormalization)                                                 
                                                                 
 dropout_7 (Dropout)         (None, 350)               0         
                                                                 
 dense_15 (Dense)            (None, 100)               35100     
                                                                 
Total params: 7,415,974
Trainab

[<tf.Variable 'stem_conv/kernel:0' shape=(3, 3, 3, 32) dtype=float32, numpy=
 array([[[[ 4.44546863e-02,  2.53470600e-01, -4.91658717e-01,
            5.52478507e-02,  6.31314695e-01, -7.53726065e-01,
            4.16245937e-01,  3.07853669e-01, -3.45844589e-02,
           -9.21582699e-01, -7.69317627e-01,  1.20296434e-01,
            1.34446576e-01,  1.12487629e-01,  1.26826334e+00,
           -1.87077343e-01,  5.61302900e-02, -4.84845787e-02,
           -9.26520303e-02, -3.09493482e-01,  7.98953235e-01,
            7.99553394e-01, -2.28657527e-03,  3.08366958e-03,
           -5.67540705e-01,  6.47983313e-01,  4.79334056e-01,
            8.63903403e-01,  1.05122782e-01,  9.45048571e-01,
           -3.68849546e-01, -6.26595616e-01],
          [ 1.25828817e-01,  7.66256332e-01, -8.03763390e-01,
            1.26664769e-02, -8.45919251e-01, -1.98657072e+00,
           -3.14825714e-01,  6.03200346e-02,  6.49157763e-01,
           -1.50864589e+00, -1.33772540e+00,  8.44407231e-02,
         

In [9]:
# 模型結構
print("Model EfficientNetV2S")
model_ENV2S.summary()

# 模型 weights
model_ENV2S.weights

Model EfficientNetV2S
Model: "sequential_3"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 efficientnetv2-s (Functiona  (None, 7, 7, 1280)       20331360  
 l)                                                              
                                                                 
 global_average_pooling2d_3   (None, 1280)             0         
 (GlobalAveragePooling2D)                                        
                                                                 
 dense_6 (Dense)             (None, 512)               655872    
                                                                 
 batch_normalization_3 (Batc  (None, 512)              2048      
 hNormalization)                                                 
                                                                 
 dropout_3 (Dropout)         (None, 512)               0         
                                

[<tf.Variable 'stem_conv/kernel:0' shape=(3, 3, 3, 24) dtype=float32, numpy=
 array([[[[-6.35806248e-02,  1.49011612e-08,  1.19282389e+00,
           -5.22850677e-02,  6.27980351e-01,  7.91157857e-02,
            6.65736079e-01, -2.56103911e-02,  7.48619318e-01,
            6.39636517e-01, -6.86916783e-02,  2.91460216e-01,
           -9.55031335e-01, -9.27215219e-01,  2.49594450e-07,
           -4.57053244e-01, -5.79332769e-01, -2.02931833e+00,
            2.10676894e-01,  5.22735655e-01, -1.13031864e+00,
           -4.82349657e-02, -5.96660972e-02,  1.32726538e+00],
          [-1.99809894e-01,  3.72529030e-08, -6.67767942e-01,
           -4.54939902e-02,  1.19455779e+00,  9.21856105e-01,
            1.53402269e+00,  1.17272675e-01,  8.69035900e-01,
            1.28043032e+00, -6.00052714e-01,  2.12217033e-01,
            7.50245035e-01, -1.73126447e+00,  1.90734863e-06,
            5.57097614e-01, -9.24793780e-01, -3.54252458e-01,
           -1.31200105e-01, -2.71736264e-01, -1.998877

In [7]:
# 預測結果（各種類機率）
pred_value_ENB4 = model_ENB4.predict(test_images)
pred_value_ENV2B1 = model_ENV2B1.predict(test_images)
pred_value_ENV2S = model_ENV2S.predict(test_images)

16/16 [==============================] - 19s 595ms/step


In [8]:
test_label_ENB4 = [pred_value_ENB4[j].argmax() for j in range(len(pred_value_ENB4))]

pred_result_ENB4 = {
    'ID' : [j for j in range(500)],
    'Category' : test_label_ENB4
}
result_ENB4 = pd.DataFrame(pred_result_ENB4)
# result_pd.to_csv('team_4_result_ENB4.csv', index = False)

In [9]:
test_label_ENV2B1 = [pred_value_ENV2B1[j].argmax() for j in range(len(pred_value_ENV2B1))]

pred_result_ENV2B1 = {
    'ID' : [j for j in range(500)],
    'Category' : test_label_ENV2B1
}
result_ENV2B1 = pd.DataFrame(pred_result_ENV2B1)
# result_pd.to_csv('team_4_result_ENV2B1.csv', index = False)

In [10]:
test_label_ENV2S = [pred_value_ENV2S[j].argmax() for j in range(len(pred_value_ENV2S))]

pred_result_ENV2S = {
    'ID' : [j for j in range(500)],
    'Category' : test_label_ENV2S
}
result_ENV2S = pd.DataFrame(pred_result_ENV2S)
# result_pd.to_csv('team_4_result_ENV2S.csv', index = False)

In [11]:
# Ensembled voting
pred_result = {
    'ID' : [j for j in range(500)],
    'Category' : [0 for j in range(500)]
}
result_pd = pd.DataFrame(pred_result)

for i in range(500):
    Cat1 = result_ENB4['Category'][i]
    Cat2 = result_ENV2B1['Category'][i]
    Cat3 = result_ENV2S['Category'][i]
    
    vote = pd.Series(data = [Cat1,Cat2,Cat3]).mode()[0]
    result_pd['Category'][i] = vote
    
result_pd.to_csv('team_4_submission.csv', index = False)